In [2]:
!pip install bertviz

  Using cached bertviz-1.4.0-py3-none-any.whl (157 kB)
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 135.8/135.8 kB 1.4 MB/s eta 0:00:00a 0:00:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 11.3/11.3 MB 36.2 MB/s eta 0:00:0000:0100:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 79.8/79.8 kB 3.0 MB/s eta 0:00:00

[notice] A new release of pip is available: 23.1.2 -> 23.3.1
[notice] To update, run: pip install --upgrade pip


In [1]:
# Use a pipeline as a high-level helper
from transformers import pipeline

pipe = pipeline("text-classification", model="JensThyregod/distilbert-base-uncased-finetuned-qnli")

# Load model directly
from transformers import AutoTokenizer, AutoModelForSequenceClassification

tokenizer = AutoTokenizer.from_pretrained("JensThyregod/distilbert-base-uncased-finetuned-qnli")
model = AutoModelForSequenceClassification.from_pretrained("JensThyregod/distilbert-base-uncased-finetuned-qnli", output_attentions=True)

In [4]:
from transformers import AutoModelForQuestionAnswering, AutoTokenizer
from bertviz import head_view, model_view

def load_transformer_model(model_path):
    """
    Load a transformer model and tokenizer from a given directory.

    :param model_path: Path to the directory containing model files.
    :return: A tuple of (model, tokenizer).
    """
    # Load pre-trained model
    model = AutoModelForQuestionAnswering.from_pretrained(model_path, output_attentions=True)
    
    # Load pre-trained model tokenizer
    tokenizer = AutoTokenizer.from_pretrained(model_path)

    return model, tokenizer


#indonesian_model_path = 'indo_xlm_roberta_qa_model'
#indonesian_model, indonesian_tokenizer = load_transformer_model(indonesian_model_path)

from datasets import load_dataset
tydiqa_dataset = load_dataset('copenlu/answerable_tydiqa')
val_dataset = tydiqa_dataset["validation"].filter(lambda example: example['language'] == 'indonesian')



def preprocess_for_visualization(examples, tokenizer):
    # Tokenize the examples
    tokenized_inputs = tokenizer(
        examples['question_text'],
        examples['document_plaintext'],
        truncation="only_second",
        max_length=512,
        return_tensors="pt",
    )
    
    return tokenized_inputs

# Example usage
example = val_dataset[-19]
#tokenized_inputs = preprocess_for_visualization(example, indonesian_tokenizer)
tokenized_inputs = preprocess_for_visualization(example, tokenizer)

def visualize_attention(model, tokenizer, tokenized_inputs):
    input_ids = tokenized_inputs['input_ids']
    token_type_ids = tokenized_inputs.get('token_type_ids')

    # If token_type_ids are not available, just use input_ids
    if token_type_ids is not None:
        attention = model(input_ids, token_type_ids=token_type_ids)[-1]
    else:
        attention = model(input_ids)[-1]
    
    # Convert inputs to lists for processing
    input_id_list = input_ids[0].tolist()
    tokens = tokenizer.convert_ids_to_tokens(input_id_list)
    
    # Find the start of the second sentence (context)
    # If token_type_ids are available, use them to find the start of the second sentence
    if token_type_ids is not None:
        sentence_b_start = token_type_ids[0].tolist().index(1)  
    else:
        # If token_type_ids are not available, you might need to find another way to determine the start of the second sentence
        # For example, you could look for the first [SEP] token
        sep_token_id = tokenizer.sep_token_id
        sentence_b_start = input_id_list.index(sep_token_id) + 1 if sep_token_id in input_id_list else 0

    #head_view(attention, tokens, sentence_b_start)
    model_view(attention, tokens, sentence_b_start)

# Visualize Attention
#visualize_attention(indonesian_model, indonesian_tokenizer, tokenized_inputs)
#Tadashi Maeda, Tomegoro Yoshizumi, S. Nishijima, S. Miyoshi, Mohammad Hatta, Soekarno, dan Achmad Soebardjo'

visualize_attention(model, tokenizer, tokenized_inputs)

<IPython.core.display.Javascript object>

In [1]:
from datasets import load_dataset
tydiqa_dataset = load_dataset('copenlu/answerable_tydiqa')
val_dataset = tydiqa_dataset["validation"].filter(lambda example: example['language'] == 'indonesian')

In [4]:
val_dataset['annotations'][-1]

{'answer_start': [-1], 'answer_text': ['']}

In [2]:

from datasets import load_dataset
tydiqa_dataset = load_dataset('copenlu/answerable_tydiqa')
val_dataset = tydiqa_dataset["validation"].filter(lambda example: example['language'] == 'indonesian')

In [3]:
for i in range(30):
    print(i)
    print(len(val_dataset[-i]['document_plaintext']))

0
592
1
1495
2
545
3
713
4
556
5
724
6
1056
7
913
8
126
9
76
10
456
11
132
12
374
13
78
14
364
15
156
16
377
17
393
18
457
19
48
20
348
21
305
22
67
23
572
24
307
25
387
26
673
27
600
28
514
29
443
